In [2]:
import tensorflow as tf
import load_data
import pickle as pkl
import networkx as nx
import scipy.sparse as sp
import numpy as np
import pandas as pd
import time

from IPython.display import HTML, clear_output
#import params

In [4]:
# get parameter values
#CMD="python3.6 load_data.py --data_dir $DATADIR --out_label_count 50 --data_serialized \
#    --training --data_mode all --data_batch_size 6 --train_max_steps 1 &> $LOGDIR/$TESTCT.log"

# parameter setup
param_dict= {}
param_dict["data_batch_size"]= 256
param_dict["data_dir"]= './data/train/'
param_dict['data_mode'] = 'all'
param_dict['data_batch_norm']= True
param_dict["data_serialized"]= True
param_dict["data_sparse"]= False
param_dict["adj_sparse"]= False #later on change it to True
param_dict["train_max_steps"]= 1000
param_dict["out_label_count"]= 50
param_dict["is_training"]= True #stop shuffling the data for code check!:) for training you should shuffle the data
# but for the validation set the shuffle off to go through each example once

# gene-gene network parameters
param_dict["network_file_name"]= '9606.STRING_experimental.edge'
param_dict["net_type"]= 'experimental'
param_dict["network_dir"]= './data/network-probe/'

# Graph Convolutional Layer params
#param_dict['GCL_dropout']= 1.
param_dict['num_features_nonzero'] = 0 #(tf.int32) in placeholder
param_dict["l2_weight_decay"]= 0 #5e-4 # 'Weight for L2 loss on embedding matrix.'
param_dict['GCL_batch_norm']= False
param_dict['CL_batch_norm']= False
param_dict['FC_batch_norm']= False



# you may need to impelement sortpooling or set2set later! I hope this works though!
#['Conv1d', 8]
# ['GC', 15]
param_dict['Arch'] = [['GC', 15],
                      ['FC', 950],
                      ['FC', 950],
                      ['FC', 50]]
        

param_dict["learning_rate"]= 0.00001 #initial learning rate
param_dict["dropout"]= 0.2 # dropout rate for train data 

param_dict['probe_length']= 841
param_dict['GraphSage_final_norm']= False
param_dict['residual_mode']= False

In [5]:
#metrics.py module
def masked_softmax_cross_entropy(preds, labels): #, mask):
    """Softmax cross-entropy loss with masking."""
    loss = tf.nn.softmax_cross_entropy_with_logits(logits=preds, labels=labels)
    return tf.reduce_mean(loss)


def masked_accuracy(preds, labels): #, mask):
    """Accuracy with masking."""
    correct_prediction = tf.equal(tf.argmax(preds, 1), tf.argmax(labels, 1))
    accuracy_all = tf.cast(correct_prediction, tf.float32)
    return tf.reduce_mean(accuracy_all)

# inits.py module
def uniform(shape, scale=0.05, name=None):
    """Uniform init."""
    initial = tf.random_uniform(shape, minval=-scale, maxval=scale, dtype=tf.float32)
    #return tf.get_variable(name, initializer= initial, trainable= True)
    return tf.Variable(initial, name=name)


def glorot(shape, name=None):
    """Glorot & Bengio (AISTATS 2010) init."""
    init_range = tf.sqrt(6/(shape[0]+shape[1]))
    init_range= tf.cast(init_range, dtype= tf.float32)
    initial = tf.random_uniform(shape, minval=-init_range, maxval=init_range, dtype=tf.float32)
    #return tf.get_variable(name, initializer= initial, trainable= True)
    return tf.Variable(initial, name=name, validate_shape=False)


def zeros(shape, name=None):
    """All zeros."""
    initial = tf.zeros(shape, dtype=tf.float32)
    #return tf.get_variable(name, initializer= initial, trainable= True)
    return tf.Variable(initial, name=name, validate_shape=False)


def ones(shape, name=None):
    """All ones."""
    initial = tf.ones(shape, dtype=tf.float32)
    #return tf.get_variable(name, initializer= initial, trainable= True)
    return tf.Variable(initial, name=name, validate_shape=False)

#preprocessing functions (later put them in preprocess.py module)
def dense_tensor_to_sparse(dense_tensor):
    a_t = dense_tensor
    # Find indices where the tensor is not zero
    idx = tf.where(tf.not_equal(a_t, 0))
    # Make the sparse tensor
    # Use tf.shape(a_t, out_type=tf.int64) instead of a_t.get_shape()
    # if tensor shape is dynamic
    sparse_tensor = tf.SparseTensor(idx, tf.gather_nd(a_t, idx), tf.shape(a_t, out_type=tf.int64))
    # Make a dense tensor back from the sparse one, only to check result is correct
    #dense = tf.sparse_tensor_to_dense(sparse_tensor)
    return sparse_tensor

def normalize_adj(adj):
    """Symmetrically normalize adjacency matrix."""
    adj= adj+tf.eye(tf.shape(adj)[0])
    rowsum= tf.reduce_sum(adj, 1)
    d_inv_sqrt = tf.pow(rowsum, -0.5)
    d_inv_sqrt= tf.reshape(d_inv_sqrt, [1, tf.size(d_inv_sqrt)])
    zero_out= tf.cast(~tf.is_inf(d_inv_sqrt), tf.float32)
    d_inv_sqrt= d_inv_sqrt*zero_out
    d_mat_inv_sqrt = tf.diag(tf.reshape(d_inv_sqrt, [tf.size(d_inv_sqrt)]))
    term1= tf.transpose(tf.matmul(adj, d_mat_inv_sqrt))
    return tf.matmul(term1, d_mat_inv_sqrt)
    
def preprocess_adj(adj,issparse):
    """Preprocessing of adjacency matrix for simple GCN model and conversion to tuple representation."""
    adj_normalized = normalize_adj(adj)
    if issparse:
        adj_normalized= dense_tensor_to_sparse(adj_normalized)
    return adj_normalized




###### graph sage adjacency normalization 
def normalize_adj_sage(adj):
    """Symmetrically normalize adjacency matrix."""
    rowsum= tf.reduce_sum(adj, 1)
    d_inv= tf.pow(rowsum, -1)
    d_inv= tf.reshape(d_inv, [1, tf.size(d_inv)])
    zero_out= tf.cast(~tf.is_inf(d_inv), tf.float32)
    d_inv= d_inv*zero_out
    d_mat_inv = tf.diag(tf.reshape(d_inv, [tf.size(d_inv)]))
    return tf.matmul(d_mat_inv, adj)

def preprocess_adj_sage(adj,issparse):
    """Preprocessing of adjacency matrix for simple GCN model and conversion to tuple representation."""
    adj_normalized = normalize_adj_sage(adj)
    if issparse:
        adj_normalized= dense_tensor_to_sparse(adj_normalized)
    return adj_normalized
###### end of graph sage adj normalization 

def build_adj(network_dict, issparse):
    graph= nx.from_dict_of_lists(network_dict)
    adj = nx.adjacency_matrix(graph,nodelist= probe_gene_order)
    # convert from scipy sparse to numpy
    adj= adj.toarray()
    adj= tf.convert_to_tensor(adj, dtype= tf.float32)
    adj_new= preprocess_adj_sage(adj,issparse)
    return adj_new, adj


def preprocess_features(features, probe_gene_order, main_gene_order, issparse):
    mask=[]
    for i, ind in enumerate(main_gene_order):
        if ind in probe_gene_order:
            mask.append(1)
        else:
            mask.append(0)
    mask= np.array(mask).reshape(1,len(mask))
    mask= np.concatenate((mask,mask), axis=1)
    
    mask= tf.convert_to_tensor(mask, dtype= tf.float32)
    features= features*mask 
    
    x= features
    intermediate_tensor = tf.reduce_sum(tf.abs(x), 0)
    zero_vector = tf.zeros(shape=(1,1), dtype=tf.float32)
    bool_mask = tf.not_equal(intermediate_tensor, zero_vector)
    #bool_mask should have only one dimension
    bool_mask= tf.reshape(bool_mask, [tf.size(bool_mask)])
    features = tf.boolean_mask(x, bool_mask, axis=1)
    # normalize the features if needed later
    
    # convert the N*(ctrl+pert= 2*G features) tensor to a 3D tensor (N,G,2)
    dim= tf.cast(tf.shape(features)[1]/2, tf.int32)
    features= tf.reshape(features, [tf.shape(features)[0],2,dim])
    features= tf.transpose(features, perm=[0, 2, 1]) # a 3-D tensor. each 2D tensor is a sample 
                         
    # convert dense tensor to sparse tensor
    if issparse:
        features= dense_tensor_to_sparse(features)
    
    # needed for tf.assign()
    features= tf.reshape(features, [param_dict["data_batch_size"], param_dict["probe_length"], 2])
    return features


#neural net classes
# layer.py module
# global unique layer ID dictionary for layer name assignment
_LAYER_UIDS = {}

def get_layer_uid(layer_name=''):
    """Helper function, assigns unique layer IDs."""
    if layer_name not in _LAYER_UIDS:
        _LAYER_UIDS[layer_name] = 1
        return 1
    else:
        _LAYER_UIDS[layer_name] += 1
        return _LAYER_UIDS[layer_name]

def sparse_dropout(x, keep_prob, noise_shape):
    """Dropout for sparse tensors."""
    random_tensor = keep_prob
    random_tensor += tf.random_uniform(noise_shape)
    dropout_mask = tf.cast(tf.floor(random_tensor), dtype=tf.bool)
    pre_out = tf.sparse_retain(x, dropout_mask)
    return pre_out * (1./keep_prob)

def dot_2D(x, y, sparse=False):
    if sparse:
        res= tf.sparse_tensor_dense_matmul(x,y)
    else:
        res= tf.matmul(x,y)
    return res # res is a 2D tensor

def dot(x, y, sparse=False, is_adj= False):
    """Wrapper for tf.matmul (sparse vs dense).""" 
    if sparse:
        if is_adj:
            # x is the adjacency(sparse) and y is the data (dense)
            orig_size= tf.shape(y)
            y= tf.transpose(y, [1,0,2])
            y= tf.reshape(y, [tf.shape(y)[0], -1])
            res= tf.sparse_tensor_dense_matmul(x,y) # res is a dense matrix
            res= tf.reshape(res, [tf.shape(res)[0],-1,orig_size[2]])
            res= tf.transpose(res,[1,0,2])
        else:
            # y is the w and x is the data which is sparse
            orig_size= tf.shape(x)
            x= tf.sparse_reshape(x, [-1,tf.shape(x)[2]])
            res= tf.sparse_tensor_dense_matmul(x,y)
            res= tf.reshape(res, [-1,orig_size[1],tf.shape(res)[1]])
    else:
        if is_adj:
            # y is the data and x is the adjacency
            #x= tf.tile(tf.expand_dims(x,0),[tf.shape(y)[0],1,1])
            #res = tf.matmul(x, y)
            orig_size= tf.shape(y)
            y= tf.transpose(y, [1,0,2])
            y= tf.reshape(y, [tf.shape(y)[0], -1])
            res= tf.matmul(x,y)
            res= tf.reshape(res, [tf.shape(res)[0],-1,orig_size[2]])
            res= tf.transpose(res,[1,0,2])
        else:
            # y is the w and x is the data
            #y= tf.tile(tf.expand_dims(y,0),[tf.shape(x)[0],1,1])
            #res = tf.matmul(x, y)
            orig_size= tf.shape(x)
            x= tf.reshape(x, [-1,tf.shape(x)[2]])
            res= tf.matmul(x,y)
            res= tf.reshape(res, [-1,orig_size[1],tf.shape(res)[1]])
    return res # res is 3D and dense

class Layer(object):
    """Base layer class. Defines basic API for all layer objects.
    Implementation inspired by keras (http://keras.io).
    # Properties
        name: String, defines the variable scope of the layer.
        logging: Boolean, switches Tensorflow histogram logging on/off
    # Methods
        _call(inputs): Defines computation graph of layer
            (i.e. takes input, returns output)
        __call__(inputs): Wrapper for _call()
        _log_vars(): Log all variables
    """

    def __init__(self, **kwargs):
        allowed_kwargs = {'name', 'logging'}
        for kwarg in kwargs.keys():
            assert kwarg in allowed_kwargs, 'Invalid keyword argument: ' + kwarg
        name = kwargs.get('name')
        if not name:
            layer = self.__class__.__name__.lower()
            name = layer + '_' + str(get_layer_uid(layer))
        self.name = name
        self.vars = {}
        logging = kwargs.get('logging', False)
        self.logging = logging
        self.sparse_inputs = False

    def _call(self, inputs):
        return inputs

    def __call__(self, inputs): #implements function called operator
        with tf.name_scope(self.name):
            if self.logging and not self.sparse_inputs:
                tf.summary.histogram(self.name + '/inputs', inputs)
            outputs = self._call(inputs)
            if self.logging:
                tf.summary.histogram(self.name + '/outputs', outputs)
            return outputs

    def _log_vars(self):
        for var in self.vars:
            tf.summary.histogram(self.name + '/vars/' + var, self.vars[var])


class GraphConvolution(Layer):
    """Graph convolution layer."""
    def __init__(self, input_dim, output_dim, placeholders, params, placeholders_val, dropout=0.,
                 sparse_inputs=False, act=tf.nn.relu, bias=False,
                 featureless=False, **kwargs):
        super(GraphConvolution, self).__init__(**kwargs)

        # modify this part later
        if dropout:
            self.dropout = placeholders_val['dropout']
        else:
            self.dropout = 0. # there is no need to initialize it as a tensor scalar

        self.act = act
        self.support = placeholders['support']
        self.sparse_inputs = sparse_inputs
        self.featureless = featureless #check later!
        self.bias = bias
        self.params= params

        # helper variable for sparse dropout
        self.num_features_nonzero = params['num_features_nonzero'] # num_features_nonzero is a tensor of unknown shape
        # fed through the placeholder
        
        with tf.variable_scope(self.name + '_vars'):
            for i in range(len(self.support)):
                self.vars['weights_' + str(i)] = glorot([input_dim, output_dim],
                                                        name='weights_' + str(i))
            if self.bias:
                self.vars['bias'] = zeros([output_dim], name='bias')

        if self.logging:
            self._log_vars()

    def _call(self, inputs):
        x = inputs

        # dropout
        if self.sparse_inputs:
            x = sparse_dropout(x, 1-self.dropout, self.num_features_nonzero)
        else:
            x = tf.nn.dropout(x, 1-self.dropout) #By default, each element is kept or dropped independently(without noise shape)

        # convolve
        supports = list()
        for i in range(len(self.support)):
            if not self.featureless:
                pre_sup = dot(x, self.vars['weights_' + str(i)], # you have to implemet dot for 3D x
                              sparse=self.sparse_inputs, is_adj= False)
            else:
                pre_sup = self.vars['weights_' + str(i)]
            support = dot(self.support[i], pre_sup, sparse=False, is_adj= True)
            supports.append(support)
        #output = tf.add_n(supports)
        output= supports[0]
        
        # bias
        if self.bias:
            output += self.vars['bias']  # assuming the output is of size batchNo*row*col and bias is of size (col)
            # the bias will be summed up with each row in the output

        output= self.act(output)
        

        if self.params['GCL_batch_norm']:
            # you need to reshape the output if you want to use this!
            with tf.variable_scope(self.name + '_vars'):
                output= tf.layers.batch_normalization(inputs= output, axis= 0,training= placeholders_val['is_training'], 
                                                      trainable= True, name= 'bn', reuse=tf.AUTO_REUSE)
        
        return output 
    
class GraphSage(Layer):    #not implemented 
    """Graph convolution layer using GraphSage algorithm."""
    def __init__(self, input_dim, output_dim, placeholders, params, placeholders_val, dropout=0.,
                 sparse_inputs=False, act=tf.nn.relu, bias=False,
                 featureless=False, **kwargs):
        super(GraphSage, self).__init__(**kwargs)

        # modify this part later
        if dropout:
            self.dropout = placeholders_val['dropout']
        else:
            self.dropout = 0. # there is no need to initialize it as a tensor scalar

        self.act = act
        self.support = placeholders['support']
        self.sparse_inputs = sparse_inputs
        self.featureless = featureless #check later!
        self.bias = bias
        self.params= params
        self.output_dim= output_dim
    
        # helper variable for sparse dropout
        self.num_features_nonzero = params['num_features_nonzero'] # num_features_nonzero is a tensor of unknown shape
        # fed through the placeholder
        
        with tf.variable_scope(self.name + '_vars'):
            for i in range(len(self.support)):
                self.vars['weights_' + str(i)] = glorot([2*input_dim, output_dim],
                                                        name='weights_' + str(i))
            if self.bias:
                self.vars['bias'] = zeros([output_dim], name='bias')

        if self.logging:
            self._log_vars()

    def _call(self, inputs):
        x = inputs

        # dropout
        if self.sparse_inputs:
            x = sparse_dropout(x, 1-self.dropout, self.num_features_nonzero)
        else:
            x = tf.nn.dropout(x, 1-self.dropout) #By default, each element is kept or dropped independently(without noise shape)

        # convolve
        supports = list()
        neighbour_mean = dot(self.support[0], x, sparse=False, is_adj= True)
        # concatenate neighbour mean with node feature itself
        x= tf.concat([neighbour_mean, x], axis= 2)
        for i in range(len(self.support)):
            if not self.featureless:
                pre_sup = dot(x, self.vars['weights_' + str(i)], # you have to implemet dot for 3D x
                              sparse=self.sparse_inputs, is_adj= False)
            else:
                pre_sup = self.vars['weights_' + str(i)]
        output= pre_sup
        
        # bias
        if self.bias:
            output += self.vars['bias']  # assuming the output is of size batchNo*row*col and bias is of size (col)
            # the bias will be summed up with each row in the output
        output= self.act(output)

        if self.params['GCL_batch_norm']:
            output= tf.reshape(output, [self.params['data_batch_size'], 
                                        self.params['probe_length'],
                                        self.output_dim])
            with tf.variable_scope(self.name + '_vars'):
                output= tf.layers.batch_normalization(inputs= output, axis= 0,training= placeholders_val['is_training'], 
                                                      trainable= True, name= 'bn', reuse=tf.AUTO_REUSE)
        
        return output 
    
class Conv_1D(Layer):
    """1D convolution layer."""
    def __init__(self, input_dim, output_dim, placeholders, params, placeholders_val, dropout=0.,
                 sparse_inputs=False, act=tf.nn.relu, bias=False,
                 featureless=False, **kwargs):
        super(Conv_1D, self).__init__(**kwargs)

        # modify this part later
        if dropout:
            self.dropout = placeholders_val['dropout']
        else:
            self.dropout = 0. # there is no need to initialize it as a tensor scalar

        self.act = act
        self.support = placeholders['support']
        self.sparse_inputs = sparse_inputs
        self.featureless = featureless #check later!
        self.bias = bias
        self.params= params
        self.output_dim= output_dim

        # helper variable for sparse dropout
        self.num_features_nonzero = params['num_features_nonzero'] # num_features_nonzero is a tensor of unknown shape
        # fed through the placeholder
        
        with tf.variable_scope(self.name + '_vars'):
            for i in range(len(self.support)):
                self.vars['weights_' + str(i)] = glorot([input_dim, output_dim],
                                                        name='weights_' + str(i))
            if self.bias:
                self.vars['bias'] = zeros([output_dim], name='bias')

        if self.logging:
            self._log_vars()

    def _call(self, inputs):
        x = inputs

        # dropout
        if self.sparse_inputs:
            x = sparse_dropout(x, 1-self.dropout, self.num_features_nonzero)
        else:
            x = tf.nn.dropout(x, 1-self.dropout) #By default, each element is kept or dropped independently(without noise shape)

        # convolve
        for i in range(len(self.support)):
            if not self.featureless:
                pre_sup = dot(x, self.vars['weights_' + str(i)], # you have to implemet dot for 3D x
                              sparse=self.sparse_inputs, is_adj= False)
            else:
                pre_sup = self.vars['weights_' + str(i)]
        output= pre_sup
        
        # bias
        if self.bias:
            output += self.vars['bias']  # assuming the output is of size batchNo*row*col and bias is of size (col)
            # the bias will be summed up with each row in the output

        output= self.act(output)
        
        if self.params['CL_batch_norm']:
            output= tf.reshape(output, [self.params['data_batch_size'], 
                            self.params['probe_length'],
                            self.output_dim])
            with tf.variable_scope(self.name + '_vars'):
                output= tf.layers.batch_normalization(inputs= output, axis= 0,training= placeholders_val['is_training'], 
                                                      trainable= True, name= 'bn', reuse=tf.AUTO_REUSE)
        return output 

    
    
class Dense(Layer):
    """Dense layer."""
    def __init__(self, input_dim, output_dim, placeholders, params,  placeholders_val, dropout=0., sparse_inputs=False,
                 act=tf.nn.relu, bias=False, featureless=False, is_2D= False, **kwargs):
        super(Dense, self).__init__(**kwargs)

        if dropout:
            self.dropout = placeholders_val['dropout']
        else:
            self.dropout = 0.

        self.act = act
        self.sparse_inputs = sparse_inputs
        self.featureless = featureless
        self.bias = bias
        self.params= params
        self.is_2D= is_2D
        self.output_dim= output_dim
        
        # helper variable for sparse dropout
        self.num_features_nonzero = params['num_features_nonzero']

        with tf.variable_scope(self.name + '_vars'):
            self.vars['weights'] = glorot([input_dim, output_dim],
                                          name='weights')
            if self.bias:
                self.vars['bias'] = zeros([output_dim], name='bias')

        if self.logging:
            self._log_vars()

    def _call(self, inputs):
        x = inputs
        
        # dropout
        if self.sparse_inputs:
            x = sparse_dropout(x, 1-self.dropout, self.num_features_nonzero)
        else:
            x = tf.nn.dropout(x, 1-self.dropout)

        # transform
        if not self.is_2D:
            x= tf.reshape(x, [-1,tf.shape(x)[1]*tf.shape(x)[2]]) # later you need to add a flag to check for the input shape
        output = dot_2D(x, self.vars['weights'], sparse=self.sparse_inputs)
        
        # bias
        if self.bias:
            output += self.vars['bias']
        
        output= self.act(output)
        
        if self.params['FC_batch_norm']:
            output= tf.reshape(output, [self.params['data_batch_size'],
                                        self.output_dim])
            with tf.variable_scope(self.name + '_vars'):
                output= tf.layers.batch_normalization(inputs= output, axis= 0,training= placeholders_val['is_training'], 
                                                      trainable= True, name= 'bn', reuse=tf.AUTO_REUSE)
        
        return output
    
# model.py module
class Model(object):
    def __init__(self, **kwargs):
        allowed_kwargs = {'name', 'logging'}
        for kwarg in kwargs.keys():
            assert kwarg in allowed_kwargs, 'Invalid keyword argument: ' + kwarg
        name = kwargs.get('name')
        if not name:
            name = self.__class__.__name__.lower()
        self.name = name

        logging = kwargs.get('logging', False)
        self.logging = logging

        self.vars = {}
        self.placeholders = {}
        self.params= {}

        self.layers = []
        self.activations = []
        self.activations_eval = []

        self.inputs = None
        self.inputs_eval = None
        self.outputs = None
        self.outputs_eval = None
        
        self.inter_out= None #to check whether the dropout works for training and validation 
        self.inter_out_eval= None

        self.loss = 0
        self.loss_eval = 0
        
        self.accuracy = 0
        self.accuracy_eval = 0
        
        self.optimizer = None
        self.opt_op = None

    def _build(self):
        raise NotImplementedError

    def build(self):
        """ Wrapper for _build() """
        with tf.variable_scope(self.name):
            self._build()

        # Build sequential layer model
        self.inputs = self.placeholders['features']
        self.inputs_norm= self.inputs 
        
        if self.params['data_batch_norm']:
            self.inputs_norm= batch_normalize(self.inputs)
            
        self.activations.append(self.inputs_norm)
        for i, layer in enumerate(self.layers):
            if self.params['residual_mode']:
                if i==2:
                    residual= tf.concat([self.activations[-2], self.activations[-1]], axis=2)
                    hidden = layer(residual)
                else:
                    hidden = layer(self.activations[-1])
            elif self.params['GraphSage_final_norm']:
                if i==2:
                    norm = tf.nn.l2_normalize(self.activations[-1], 2)
                    hidden= layer(norm)
                else:
                    hidden = layer(self.activations[-1])
            else:
                hidden = layer(self.activations[-1])
            self.activations.append(hidden)
        self.outputs = self.activations[-1]

        # Store model variables for easy access
        variables = tf.get_collection(tf.GraphKeys.GLOBAL_VARIABLES, scope=self.name)
        self.vars = {var.name: var for var in variables}

        # Build metrics
        self._loss()
        self._accuracy()

        self.opt_op = self.optimizer.minimize(self.loss)
    
    def parameter_count(self):
        return len(self.vars.keys())
        
    def build_eval(self):
        # Build sequential layer model
        self.inputs_eval = self.placeholders['features_eval']
        self.inputs_norm_eval= self.inputs_eval 
        
        if self.params['data_batch_norm']:
            self.inputs_norm_eval= batch_normalize(self.inputs_eval)
           
        self.activations_eval.append(self.inputs_norm_eval)
        for i, layer in enumerate(self.layers):
            if self.params['residual_mode']:
                if i==2:
                    residual= tf.concat([self.activations_eval[-2], self.activations_eval[-1]], axis=2)
                    hidden = layer(residual)
                else:
                    hidden = layer(self.activations_eval[-1])
            elif self.params['GraphSage_final_norm']:
                if i==2:
                    norm = tf.nn.l2_normalize(self.activations_eval[-1], 2)
                    hidden= layer(norm)
                else:
                    hidden = layer(self.activations_eval[-1])
            else:
                hidden = layer(self.activations_eval[-1])
            self.activations_eval.append(hidden)
        self.outputs_eval = self.activations_eval[-1]

        # Build metrics
        self._loss_eval()
        self._accuracy_eval()


    def predict(self):
        pass

    def _loss(self):
        raise NotImplementedError

    def _accuracy(self):
        raise NotImplementedError
        
    
    def _loss_eval(self):
        raise NotImplementedError

    def _accuracy_eval(self):
        raise NotImplementedError
        
    def update_field(features_alter, labels_alter):
        pass

    def save(self, sess=None):
        if not sess:
            raise AttributeError("TensorFlow session not provided.")
        saver = tf.train.Saver(self.vars)
        save_path = saver.save(sess, "./model-save/tmp/%s.ckpt" % self.name)
        print("Model saved in file: %s" % save_path)

    def load(self, sess=None, save_path= '/model-save/tmp/'):
        if not sess:
            raise AttributeError("TensorFlow session not provided.")
        saver = tf.train.Saver(self.vars)
        #save_path = "./visual-save-load/tmp/%s.ckpt" % self.name
        saver.restore(sess, tf.train.latest_checkpoint(save_path))
        print("Model restored from file: %s" % save_path)
           

class GCN(Model):
    def __init__(self, placeholders, params, input_dim, placeholders_val, **kwargs):
        super(GCN, self).__init__(**kwargs)
        
        self.input_dim = input_dim
        #self.input_dim = self.inputs.get_shape().as_list()[2]  # To be supported in future Tensorflow versions
        #self.output_dim = placeholders['labels'].get_shape().as_list()[1]
        self.output_dim= tf.shape(placeholders['labels'])[1]
        self.placeholders = placeholders
        self.params= params
        self.output_average= 0.
        self.placeholders_val= placeholders_val

        self.optimizer = tf.train.AdamOptimizer(learning_rate=params["learning_rate"])

        self.build()
        self.build_eval()
        

    #def update_field(self, dic={}):
    #    self.placeholders= dic
    #    self.inputs= self.placeholders['features']
        
    def _loss(self):  # should be implemented
        # Weight decay loss
        for var in self.layers[0].vars.values():
            pass
            #self.loss += self.params["l2_weight_decay"] * tf.nn.l2_loss(var)

        # Cross entropy error
        self.loss += masked_softmax_cross_entropy(self.outputs, self.placeholders['labels'])#,
                                                  #self.placeholders['labels_mask'])
    
    def _loss_eval(self):  # should be implemented
        # Weight decay loss
        for var in self.layers[0].vars.values():
            pass
            #self.loss += self.params["l2_weight_decay"] * tf.nn.l2_loss(var)

        # Cross entropy error
        self.loss_eval += masked_softmax_cross_entropy(self.outputs_eval, self.placeholders['labels_eval'])#,
                                                  #self.placeholders['labels_mask'])
    
    def output_avg(self):
        self.out_avg, self.out_std = tf.nn.moments(tf.reshape(self.outputs,[-1]), axes=[0])

    def _accuracy(self): # should be implemented
        self.accuracy = masked_accuracy(self.outputs, self.placeholders['labels']) #,
                                        #self.placeholders['labels_mask'])
    def _accuracy_eval(self): # should be implemented
        self.accuracy_eval = masked_accuracy(self.outputs_eval, self.placeholders['labels_eval']) #,
                                        #self.placeholders['labels_mask'])

    def _build(self):
        in_dim = self.input_dim
        layer_constructors = {'GC': GraphSage,
                              'CONV1D': Conv_1D,
                              'FC': Dense,
                              'FC_SPEC': Dense}
        
        for i, [layer_type, out_dim] in enumerate(self.params['Arch']):
            assert layer_type.upper() in list(layer_constructors.keys())
            layer_const = layer_constructors[layer_type.upper()]
            
            # cancatenation of the CL and GL features
            if self.params['residual_mode']:
                if i==2:
                    in_dim= 2*in_dim
                    
            kwargs = dict(input_dim= in_dim,
                          output_dim=out_dim,
                          placeholders=self.placeholders,
                          placeholders_val= self.placeholders_val,
                          params= self.params,
                          act=tf.nn.relu, # not sure about activation
                          dropout=True, # not sure about dropout implementation
                          sparse_inputs=False,
                          bias= True,
                          logging=self.logging)
            
#             #Special accomodations for FC_SPEC
#             if layer_type.upper() == 'FC_SPEC':
#                 kwargs['input_dim'] = kwargs['input_dim'] * self.params["probe_length"]
#                 kwargs['is_2D'] = False
#             if layer_type.upper() == 'FC':
#                 #if not(self.params['Arch'][i-1][0] == 'FC'):
#                 #    kwargs['input_dim'] = kwargs['input_dim'] * self.params["probe_length"]
#                 #    kwargs['is_2D'] = False
#                 #else:
                
#                 if i == (len(self.params['Arch'])-1):
#                     kwargs['act'] = lambda x: x
                        
                        
            #Special accomodations for FC
            if layer_type.upper() == 'FC':
                if not(self.params['Arch'][i-1][0] == 'FC'):
                    kwargs['input_dim'] = kwargs['input_dim'] * self.params["probe_length"]
                    kwargs['is_2D'] = False
                else:
                    kwargs['is_2D'] = True
                
                if i == (len(self.params['Arch'])-1):
                    kwargs['act'] = lambda x: x
            
            self.layers.append(layer_const(**kwargs))
            in_dim = out_dim
            

    def predict(self):
        return tf.nn.softmax(self.outputs)


def batch_normalize(orig_values):
    """normalize layer across batch"""
    [mean, var] = tf.nn.moments(orig_values, 0)
    norm_values = tf.nn.batch_normalization(orig_values, mean, var,
                                            offset=None,
                                            scale=None,
                                            variance_epsilon=1e-3)
    return norm_values

# placeholder for validation
def construct_feed_dict(dropout, is_training, placeholders):
    """Construct feed dictionary."""
    feed_dict = dict()
    feed_dict.update({placeholders['dropout']: dropout})
    feed_dict.update({placeholders['is_training']: is_training})
    return feed_dict

In [6]:
def count_params(var_list):
    param_counts = []
    for variable in var_list:
        variable_parameters = 1
        shape = variable.get_shape()
        for dim in shape:
            variable_parameters *= dim.value
        param_counts.append(variable_parameters)
    return np.sum(param_counts)

In [7]:
with tf.device('/device:GPU:0'):
    # main body 
    # loading the data (network and node features)
    feat_b, label_b, meta_b, input_size, nummeta, numexamps = load_data.get_batch(param_dict, True)

    print("data final input_size: " + str(input_size), file= open('printout','a'))
    print("data nummeta: " + str(nummeta), file= open('printout','a'))

    # loading the interaction network and probe gene order then bulding adjacency
    saved_list_names= [param_dict["network_file_name"], 
                       'probe_gene_order_'+param_dict["net_type"], 'main_gene_order']
    objects= []
    for i, name in enumerate(saved_list_names):
        infile = open(param_dict["network_dir"]+name+'.pkl',"rb")
        objects.append(pkl.load(infile))
    infile.close()

    network_dict, probe_gene_order, main_gene_order= tuple(objects)

### start load_data
data class_column: 1957
data num_metadata: 24
data num_examples: 50000
data number of datafiles: 1
data example datafile: ./data/train/file0.tfrecord
data batch_size: 256
data nreaders: 1
Instructions for updating:
To construct input pipelines, use the `tf.data` module.
Instructions for updating:
To construct input pipelines, use the `tf.data` module.
data orig input_size: 1956
data final input_size: 1956


In [8]:
with tf.device('/device:GPU:0'):
    param_dict['train_max_steps']= 400000 #5
    param_dict["save_freq"]= int(50000/param_dict['data_batch_size']) # 1 # 391 # int(50000/param_dict['data_batch_size'])

    # setup for validation dataset 
    param_dict_eval= param_dict.copy()
    param_dict_eval["data_dir"]= './data/eval/'
    param_dict_eval['eval_max_steps']= int(5000/param_dict_eval['data_batch_size']) #1
    param_dict_eval['dropout']= 0.
    param_dict_eval['is_training']= False
    #param_dict_eval['data_batch_size']= 500

    # building adj matrix (sparse)
    adj_new, adj_prev= build_adj(network_dict, param_dict['adj_sparse'])

    # preprocess the first batch of features
    features_new= preprocess_features(feat_b, probe_gene_order, main_gene_order, param_dict['data_sparse'])
    true_labels_one_hot = tf.one_hot(label_b, depth=param_dict['out_label_count'],
                                             on_value=1., off_value=0., dtype= tf.float32) #  a tensor with shape (sample_size, number of classes)

    # loading the validation data
    feat_eval_b, label_eval_b, meta_eval_b, input_eval_size, nummeta_eval, numexamps_eval = load_data.get_batch(param_dict_eval, True)
    # preprocess the first batch of features
    features_new_eval= preprocess_features(feat_eval_b, probe_gene_order, main_gene_order, param_dict_eval['data_sparse'])
    true_labels_one_hot_eval = tf.one_hot(label_eval_b, depth=param_dict_eval['out_label_count'],
                                             on_value=1., off_value=0., dtype= tf.float32) #  a tensor with shape (sample_size, number of classes)

    # holder dict will be extended later
    holder= {'features': features_new, 'labels': true_labels_one_hot, 'support': [adj_new], 
             'features_eval': features_new_eval, 'labels_eval': true_labels_one_hot_eval}

### start load_data
data class_column: 1957
data num_metadata: 24
data num_examples: 5000
data number of datafiles: 1
data example datafile: ./data/eval/file0.tfrecord
data batch_size: 256
data nreaders: 1
data orig input_size: 1956
data final input_size: 1956


In [9]:
with tf.device('/device:GPU:0'): # there might be a problem doing it within gpu or not !!!!!!! 
    placeholders_val= {'dropout': tf.placeholder_with_default(0., shape=()),
                       'is_training': tf.placeholder_with_default(True, shape=())}
    feed_dict= construct_feed_dict(param_dict['dropout'], param_dict['is_training'], placeholders_val)

    # Create model
    model = GCN(holder, param_dict, input_dim=tf.shape(features_new)[2], placeholders_val= placeholders_val, logging=True)
    
    vars_names = list(model.vars.keys())
    vars_shapes = [tf.shape(model.vars[key]) for _,key in enumerate(vars_names)]
    
    model.output_avg()
    save_freq= param_dict["save_freq"]
    valid_freq= 391  #int(50000/param_dict['data_batch_size'])

sess= tf.Session(config=tf.ConfigProto(allow_soft_placement= True))

coord = tf.train.Coordinator()
threads = tf.train.start_queue_runners(coord=coord, sess=sess)
print("data feat_batch, label_batch, meta_batch: ", file= open('printout','a'))

# initialize the queue threads to start to shovel data
ALL_EVAL_ACC= []
ALL_EVAL_LOSS= []

# making summaries for model
tf.summary.scalar("tarin_loss", model.loss)
tf.summary.scalar("train_accuracy", model.accuracy)
tf.summary.scalar("eval_loss", model.loss_eval)
tf.summary.scalar("eval_accuracy", model.accuracy_eval)


merged_summary= tf.summary.merge_all()
writer = tf.summary.FileWriter("./summaries/", sess.graph)

sess.run(tf.initializers.global_variables())
#model.load(sess)

# model param statistics 
print_shapes=True
if print_shapes:
    shape_data = []
    np_var_shapes = sess.run(vars_shapes)
    for i,var_name in enumerate(vars_names):
        shape_data.append([var_name, np.prod(np_var_shapes[i]), np_var_shapes[i]])
        #print(var_name+' : \t\t\t\t '+str(np_var_shapes[i]) + ' : \t\t\t\t ' + str(np.prod(np_var_shapes[i])))
        df = pd.DataFrame(shape_data,columns=['Variable','Parameters', 'Shape'])
    print(df)


for step in range(param_dict["train_max_steps"]):
    print("data train_step: " + str(step),file= open('printout','a'))
    print(step, file= open('printout','a'))

    # Train model
    t = time.time()


    # Training step
    outs = sess.run([model.opt_op, model.loss, model.accuracy, 
                     model.out_avg, model.out_std, model.inputs, model.outputs], feed_dict= feed_dict)

    if (step%save_freq==0):
         model.save(sess)


    if step%valid_freq == 0:
        feed_dict.update({placeholders_val['dropout']: param_dict_eval['dropout']})
        feed_dict.update({placeholders_val['is_training']: param_dict_eval['is_training']})

        outs_val = sess.run([model.loss_eval, model.accuracy_eval, 
                      model.inputs_eval, model.outputs_eval], feed_dict= feed_dict)
        summ= sess.run(merged_summary)
        writer.add_summary(summ, step)

        feed_dict.update({placeholders_val['dropout']: param_dict['dropout']})
        feed_dict.update({placeholders_val['is_training']: param_dict['is_training']})

        # Print results
        print("Epoch:", '%04d' % (step + 1),"val_loss= ", "{:.5f}".format(outs_val[0]),
              "val_accuracy= ", "{:.5f}".format(outs_val[1]))

    print("Epoch:", '%04d' % (step + 1), "train_loss=", "{:.5f}".format(outs[1]),
          "train_acc=", "{:.5f}".format(outs[2]), "out_avg=", "{:.5f}".format(outs[3]),
          "out_std=", "{:.5f}".format(outs[4]))

print("Optimization Finished!")
# We request our child threads to stop ...
coord.request_stop()
# ... and we wait for them to do so before releasing the main thread
coord.join(threads)


Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.

Instructions for updating:
To construct input pipelines, use the `tf.data` module.
                     Variable  Parameters        Shape
0  gcn/dense_1_vars/weights:0     1597900  [1682, 950]
1     gcn/dense_1_vars/bias:0         950        [950]
2  gcn/dense_2_vars/weights:0      902500   [950, 950]
3     gcn/dense_2_vars/bias:0         950        [950]
4  gcn/dense_3_vars/weights:0      902500   [950, 950]
5     gcn/dense_3_vars/bias:0         950        [950]
6  gcn/dense_4_vars/weights:0       47500    [950, 50]
7     gcn/dense_4_vars/bias:0          50         [50]
Model saved in file: ./model-save/tmp/gcn.ckpt
Epoch: 0001 val_loss=  4.01514 val_accuracy=  0.01562
Epoch: 0001 train_loss= 4.23133 train_acc= 0.01562 out_avg= 0.07457 out_std= 0.66861
Epoch: 0002 train_loss= 4.25173 train_acc= 0.

Epoch: 0083 train_loss= 4.05360 train_acc= 0.03125 out_avg= 0.08302 out_std= 0.36525
Epoch: 0084 train_loss= 4.04846 train_acc= 0.03125 out_avg= 0.08533 out_std= 0.35878
Epoch: 0085 train_loss= 4.00367 train_acc= 0.01953 out_avg= 0.07470 out_std= 0.36688
Epoch: 0086 train_loss= 4.04633 train_acc= 0.02734 out_avg= 0.09047 out_std= 0.36205
Epoch: 0087 train_loss= 4.02412 train_acc= 0.01953 out_avg= 0.08099 out_std= 0.36060
Epoch: 0088 train_loss= 4.09428 train_acc= 0.02734 out_avg= 0.08782 out_std= 0.36814
Epoch: 0089 train_loss= 4.06513 train_acc= 0.02344 out_avg= 0.07538 out_std= 0.36651
Epoch: 0090 train_loss= 4.03217 train_acc= 0.05469 out_avg= 0.08478 out_std= 0.37426
Epoch: 0091 train_loss= 4.03007 train_acc= 0.00781 out_avg= 0.07253 out_std= 0.35784
Epoch: 0092 train_loss= 4.07273 train_acc= 0.02734 out_avg= 0.07973 out_std= 0.36377
Epoch: 0093 train_loss= 4.06041 train_acc= 0.01172 out_avg= 0.07534 out_std= 0.35875
Epoch: 0094 train_loss= 4.05697 train_acc= 0.03125 out_avg= 0.085

Epoch: 0181 train_loss= 4.00095 train_acc= 0.03125 out_avg= 0.06290 out_std= 0.32755
Epoch: 0182 train_loss= 3.95240 train_acc= 0.02344 out_avg= 0.06448 out_std= 0.32248
Epoch: 0183 train_loss= 3.92804 train_acc= 0.05078 out_avg= 0.07659 out_std= 0.32014
Epoch: 0184 train_loss= 3.94346 train_acc= 0.03125 out_avg= 0.08230 out_std= 0.32420
Epoch: 0185 train_loss= 3.97790 train_acc= 0.03125 out_avg= 0.07813 out_std= 0.31212
Epoch: 0186 train_loss= 3.98791 train_acc= 0.03125 out_avg= 0.07521 out_std= 0.31650
Epoch: 0187 train_loss= 4.06681 train_acc= 0.01562 out_avg= 0.07723 out_std= 0.32020
Epoch: 0188 train_loss= 3.98646 train_acc= 0.01953 out_avg= 0.07607 out_std= 0.31419
Epoch: 0189 train_loss= 4.00684 train_acc= 0.01562 out_avg= 0.08332 out_std= 0.31221
Epoch: 0190 train_loss= 4.01771 train_acc= 0.02344 out_avg= 0.06507 out_std= 0.31818
Epoch: 0191 train_loss= 3.91796 train_acc= 0.02734 out_avg= 0.06631 out_std= 0.31052
Epoch: 0192 train_loss= 4.03490 train_acc= 0.01953 out_avg= 0.068

Epoch: 0278 train_loss= 3.92310 train_acc= 0.02734 out_avg= 0.06187 out_std= 0.29806
Epoch: 0279 train_loss= 3.97902 train_acc= 0.02344 out_avg= 0.06308 out_std= 0.29158
Epoch: 0280 train_loss= 3.96403 train_acc= 0.02344 out_avg= 0.06165 out_std= 0.29310
Epoch: 0281 train_loss= 3.95774 train_acc= 0.05078 out_avg= 0.06248 out_std= 0.29341
Epoch: 0282 train_loss= 3.94657 train_acc= 0.03125 out_avg= 0.06595 out_std= 0.29179
Epoch: 0283 train_loss= 3.94048 train_acc= 0.03125 out_avg= 0.05985 out_std= 0.29601
Epoch: 0284 train_loss= 3.95473 train_acc= 0.03125 out_avg= 0.06152 out_std= 0.29301
Epoch: 0285 train_loss= 4.01669 train_acc= 0.03125 out_avg= 0.06020 out_std= 0.29538
Epoch: 0286 train_loss= 3.96480 train_acc= 0.04297 out_avg= 0.06455 out_std= 0.29314
Epoch: 0287 train_loss= 3.93693 train_acc= 0.05469 out_avg= 0.06339 out_std= 0.29871
Epoch: 0288 train_loss= 3.91250 train_acc= 0.05859 out_avg= 0.05510 out_std= 0.29161
Epoch: 0289 train_loss= 3.95354 train_acc= 0.03516 out_avg= 0.066

Epoch: 0375 train_loss= 3.94907 train_acc= 0.03906 out_avg= 0.06130 out_std= 0.28369
Epoch: 0376 train_loss= 3.96659 train_acc= 0.03516 out_avg= 0.06054 out_std= 0.28438
Epoch: 0377 train_loss= 3.92195 train_acc= 0.02734 out_avg= 0.05645 out_std= 0.28427
Epoch: 0378 train_loss= 3.90760 train_acc= 0.06250 out_avg= 0.06405 out_std= 0.28617
Epoch: 0379 train_loss= 3.94852 train_acc= 0.04688 out_avg= 0.06692 out_std= 0.28555
Epoch: 0380 train_loss= 3.94925 train_acc= 0.02734 out_avg= 0.06243 out_std= 0.28771
Epoch: 0381 train_loss= 3.91135 train_acc= 0.03516 out_avg= 0.06047 out_std= 0.28356
Epoch: 0382 train_loss= 3.86781 train_acc= 0.03906 out_avg= 0.05714 out_std= 0.27604
Epoch: 0383 train_loss= 3.88577 train_acc= 0.04688 out_avg= 0.05654 out_std= 0.28528
Epoch: 0384 train_loss= 3.90349 train_acc= 0.05078 out_avg= 0.06115 out_std= 0.27721
Epoch: 0385 train_loss= 3.88598 train_acc= 0.03516 out_avg= 0.05982 out_std= 0.28038
Epoch: 0386 train_loss= 3.84387 train_acc= 0.06641 out_avg= 0.054

...

Epoch: 52579 train_loss= 1.15203 train_acc= 0.62500 out_avg= -0.94879 out_std= 12.76609
Epoch: 52580 train_loss= 0.89773 train_acc= 0.73047 out_avg= -0.93763 out_std= 12.79599
Epoch: 52581 train_loss= 0.96931 train_acc= 0.69531 out_avg= -0.91986 out_std= 12.49797
Epoch: 52582 train_loss= 0.97749 train_acc= 0.69141 out_avg= -0.94219 out_std= 12.84911
Epoch: 52583 train_loss= 1.14194 train_acc= 0.64062 out_avg= -0.94713 out_std= 12.65658
Epoch: 52584 train_loss= 0.95581 train_acc= 0.73047 out_avg= -0.94571 out_std= 13.03959
Epoch: 52585 train_loss= 0.87025 train_acc= 0.75781 out_avg= -0.92929 out_std= 12.98481
Epoch: 52586 train_loss= 0.93128 train_acc= 0.70312 out_avg= -0.95471 out_std= 12.96631
Epoch: 52587 train_loss= 1.05935 train_acc= 0.65625 out_avg= -0.98368 out_std= 13.79197
Epoch: 52588 train_loss= 0.84662 train_acc= 0.77344 out_avg= -0.94918 out_std= 13.32236
Epoch: 52589 train_loss= 0.99301 train_acc= 0.69531 out_avg= -0.95045 out_std= 12.98953
Epoch: 52590 train_loss= 0.92395

Epoch: 52672 train_loss= 0.92119 train_acc= 0.71875 out_avg= -0.94110 out_std= 12.23082
Epoch: 52673 train_loss= 0.96155 train_acc= 0.68750 out_avg= -0.94637 out_std= 12.73018
Epoch: 52674 train_loss= 0.95387 train_acc= 0.71875 out_avg= -0.95669 out_std= 12.66635
Epoch: 52675 train_loss= 0.87418 train_acc= 0.73047 out_avg= -0.95265 out_std= 13.53688
Epoch: 52676 train_loss= 0.85150 train_acc= 0.75391 out_avg= -0.92377 out_std= 12.49834
Epoch: 52677 train_loss= 0.88461 train_acc= 0.72266 out_avg= -0.96021 out_std= 12.89155
Epoch: 52678 train_loss= 0.93465 train_acc= 0.73438 out_avg= -0.95588 out_std= 13.43686
Epoch: 52679 train_loss= 0.93499 train_acc= 0.71875 out_avg= -0.95657 out_std= 12.71373
Epoch: 52680 train_loss= 1.04477 train_acc= 0.68750 out_avg= -0.93695 out_std= 12.61743
Epoch: 52681 train_loss= 1.04355 train_acc= 0.69531 out_avg= -0.96932 out_std= 13.54393
Epoch: 52682 train_loss= 1.01535 train_acc= 0.66406 out_avg= -0.95345 out_std= 13.05084
Epoch: 52683 train_loss= 0.88090

Epoch: 52766 train_loss= 1.05954 train_acc= 0.67188 out_avg= -0.93589 out_std= 12.34397
Epoch: 52767 train_loss= 1.06085 train_acc= 0.66016 out_avg= -0.94407 out_std= 12.88188
Epoch: 52768 train_loss= 1.04346 train_acc= 0.71094 out_avg= -0.93559 out_std= 12.62779
Epoch: 52769 train_loss= 0.91914 train_acc= 0.73047 out_avg= -0.92853 out_std= 12.52105
Epoch: 52770 train_loss= 1.00627 train_acc= 0.70703 out_avg= -0.94786 out_std= 12.83901
Epoch: 52771 train_loss= 1.05374 train_acc= 0.67188 out_avg= -0.93906 out_std= 12.50936
Epoch: 52772 train_loss= 0.95879 train_acc= 0.71484 out_avg= -0.94215 out_std= 13.15112
Epoch: 52773 train_loss= 0.89475 train_acc= 0.71484 out_avg= -0.97693 out_std= 13.65994
Epoch: 52774 train_loss= 0.84840 train_acc= 0.74609 out_avg= -0.94880 out_std= 12.87508
Epoch: 52775 train_loss= 0.97079 train_acc= 0.70312 out_avg= -0.93560 out_std= 12.87398
Epoch: 52776 train_loss= 0.85741 train_acc= 0.71875 out_avg= -0.95175 out_std= 13.07201
Epoch: 52777 train_loss= 0.82933

Epoch: 52859 train_loss= 0.92740 train_acc= 0.70703 out_avg= -0.94860 out_std= 13.07323
Epoch: 52860 train_loss= 1.05652 train_acc= 0.71484 out_avg= -0.93633 out_std= 13.12534
Epoch: 52861 train_loss= 0.89128 train_acc= 0.74219 out_avg= -0.95345 out_std= 13.14900
Epoch: 52862 train_loss= 1.01709 train_acc= 0.68359 out_avg= -0.94114 out_std= 12.98900
Epoch: 52863 train_loss= 0.94420 train_acc= 0.69141 out_avg= -0.93173 out_std= 12.74894
Epoch: 52864 train_loss= 1.00396 train_acc= 0.66797 out_avg= -0.92291 out_std= 12.44360
Epoch: 52865 train_loss= 1.04644 train_acc= 0.68359 out_avg= -0.95539 out_std= 13.31301
Epoch: 52866 train_loss= 0.78938 train_acc= 0.76562 out_avg= -0.94137 out_std= 13.27265
Epoch: 52867 train_loss= 0.83620 train_acc= 0.75000 out_avg= -0.96300 out_std= 13.26882
Epoch: 52868 train_loss= 1.03638 train_acc= 0.69922 out_avg= -0.93127 out_std= 12.35620
Epoch: 52869 train_loss= 0.85167 train_acc= 0.75000 out_avg= -0.92707 out_std= 12.61201
Epoch: 52870 train_loss= 1.03180

KeyboardInterrupt: 

In [ ]:
# calculate the accuracy over the whole validation set

In [ ]:
############## Validation and test ###############################
# with tf.device('/device:GPU:0'):
#     placeholders_val= {'dropout': tf.placeholder_with_default(0., shape=()),
#                        'is_training': tf.placeholder_with_default(True, shape=())}
#     feed_dict= construct_feed_dict(param_dict['dropout'], param_dict['is_training'], placeholders_val)

#     # Create model
#     model = GCN(holder, param_dict, input_dim=tf.shape(features_new)[2], placeholders_val= placeholders_val, logging=True)
#     model.output_avg()
#     save_freq= param_dict["save_freq"]
#     valid_freq= 391

    

# sess= tf.Session(config=tf.ConfigProto(allow_soft_placement= True))    
# coord = tf.train.Coordinator()
# threads = tf.train.start_queue_runners(coord=coord, sess=sess)
# print("data feat_batch, label_batch, meta_batch: ", file= open('printout','a'))

# # initialize the queue threads to start to shovel data
# # initialize the variable

# ALL_EVAL_ACC= []
# ALL_EVAL_LOSS= []


# sess.run(tf.initializers.global_variables())
# model.load(sess, save_path='./model-save/tmp/')

# dev_steps= int(np.ceil(500/256))
# for step in range(dev_steps):
#     # Train model
#     t = time.time()
    

#     feed_dict.update({placeholders_val['dropout']: param_dict_eval['dropout']})
#     feed_dict.update({placeholders_val['is_training']: param_dict_eval['is_training']})
    
#     outs_val = sess.run([model.loss_eval, model.accuracy_eval, 
#                          model.inputs_eval, model.outputs_eval, model.inter_out_eval], feed_dict= feed_dict)
#     ALL_EVAL_LOSS.append(outs_val[0])
#     ALL_EVAL_ACC.append(outs_val[1])
    
#     # Print results
#     print("Epoch:", '%04d' % (step + 1),"val_loss= ", "{:.5f}".format(outs_val[0]),
#           "val_accuracy= ", "{:.5f}".format(outs_val[1]))
    
# print("Optimization Finished!")
# print('total validation loss: ', sum(ALL_EVAL_LOSS)/len(ALL_EVAL_LOSS))
# print('total validation accuracy: ', sum(ALL_EVAL_ACC)/len(ALL_EVAL_ACC))


# # We request our child threads to stop ...
# coord.request_stop()
# # ... and we wait for them to do so before releasing the main thread
# coord.join(threads)


In [ ]:
a= np.array([[[0,0,0],[3,8,4]],[[1,2,2],[3,8,4]]])
a_tf= tf.convert_to_tensor(a, dtype=tf.float32)
norm= tf.nn.l2_normalize(a_tf, 2)
sess= tf.Session()
#norm= tf.norm(a_tf, axis= 2)
#norm= tf.reshape(norm, [2,2,1])
print(sess.run(norm))
#print(sess.run(a_tf/norm))

In [ ]:
[[3.      ]
 [9.433981]]
[[0.33333334 0.6666667  0.6666667 ]
 [0.31799936 0.8479983  0.42399916]]

In [ ]:
import numpy as np 
import tensorflow as tf

a= np.array([[[0,0,0],[3,8,4]],[[1,2,2],[3,8,4]]])
a_tf= tf.convert_to_tensor(a, dtype=tf.float32)
sess= tf.Session()
#a_tf= tf.clip_by_value(a_tf, 1e-37, 1e37)

print(sess.run(a_tf))